In [21]:
%reload_ext autoreload
%autoreload 2

In [22]:
import os,sys
import re
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler

os.chdir('..')

In [23]:
from src.data_preprocess import DataPreProcessor
preprocessor = DataPreProcessor()

df = preprocessor.fetch_preprocessed_data()




In [24]:
df.columns

Index(['Bearer Id', 'Start', 'Start ms', 'End', 'End ms', 'Dur. (ms)', 'IMSI',
       'MSISDN/Number', 'IMEI', 'Last Location Name', 'Avg RTT DL (ms)',
       'Avg RTT UL (ms)', 'Avg Bearer TP DL (kbps)', 'Avg Bearer TP UL (kbps)',
       'TCP DL Retrans. Vol (Bytes)', 'TCP UL Retrans. Vol (Bytes)',
       'DL TP < 50 Kbps (%)', '50 Kbps < DL TP < 250 Kbps (%)',
       '250 Kbps < DL TP < 1 Mbps (%)', 'DL TP > 1 Mbps (%)',
       'UL TP < 10 Kbps (%)', '10 Kbps < UL TP < 50 Kbps (%)',
       '50 Kbps < UL TP < 300 Kbps (%)', 'UL TP > 300 Kbps (%)',
       'HTTP DL (Bytes)', 'HTTP UL (Bytes)', 'Activity Duration DL (ms)',
       'Activity Duration UL (ms)', 'Dur. (ms).1', 'Handset Manufacturer',
       'Handset Type', 'Nb of sec with 125000B < Vol DL',
       'Nb of sec with 1250B < Vol UL < 6250B',
       'Nb of sec with 31250B < Vol DL < 125000B',
       'Nb of sec with 37500B < Vol UL',
       'Nb of sec with 6250B < Vol DL < 31250B',
       'Nb of sec with 6250B < Vol UL < 37500B',


In [36]:
customer_info = df.groupby('MSISDN/Number').agg({
    'TCP DL Retrans. Vol (Bytes)': 'mean',
    # 'TCP UL Retrans. Vol (Bytes)': 'mean',
    'Avg RTT DL (ms)': 'mean',
    # 'Avg RTT UL (ms)': 'mean',
    'Handset Type': 'first',
    'Avg Bearer TP DL (kbps)': 'mean',
    # 'Avg Bearer TP UL (kbps)': 'mean'
})

In [59]:

# Task 4.2: List top, bottom, and most frequent TCP, RTT, and throughput values
top_10_tcp = df['TCP DL Retrans. Vol (Bytes)'].nlargest(10)
bottom_10_tcp = df['TCP DL Retrans. Vol (Bytes)'].nsmallest(10)
most_frequent_tcp = df['TCP DL Retrans. Vol (Bytes)'].mode()

top_10_rtt = df['Avg RTT DL (ms)'].nlargest(10)
bottom_10_rtt = df['Avg RTT DL (ms)'].nsmallest(10)
most_frequent_rtt = df['Avg RTT DL (ms)'].mode()

top_10_throughput = df['Avg Bearer TP DL (kbps)'].nlargest(10)
bottom_10_throughput = df['Avg Bearer TP DL (kbps)'].nsmallest(10)
most_frequent_throughput = df['Avg Bearer TP DL (kbps)'].mode()


In [60]:
# Top 10 Throughput values
top_10_throughput = pd.concat([df['Avg Bearer TP DL (kbps)'], df['Avg Bearer TP UL (kbps)']]).nlargest(10)
# Bottom 10 Throughput values
bottom_10_throughput = pd.concat([df['Avg Bearer TP DL (kbps)'], df['Avg Bearer TP UL (kbps)']]).nsmallest(10)
# Most frequent Throughput values
most_frequent_throughput = pd.concat([df['Avg Bearer TP DL (kbps)'], df['Avg Bearer TP UL (kbps)']]).value_counts().head(10)

In [38]:
print("Top 10 TCP values:\n", top_10_tcp)
print("\nBottom 10 TCP values:\n", bottom_10_tcp)
print("\nMost frequent TCP value:", most_frequent_tcp.values[0])
print("\nTop 10 RTT values:\n", top_10_rtt)
print("\nBottom 10 RTT values:\n", bottom_10_rtt)
print("\nMost frequent RTT value:", most_frequent_rtt.values[0])
print("\nTop 10 throughput values:\n", top_10_throughput)
print("\nBottom 10 throughput values:\n", bottom_10_throughput)
print("\nMost frequent throughput value:", most_frequent_throughput.values[0])


Top 10 TCP values:
 77985     4.294426e+09
135678    4.291380e+09
34647     4.289877e+09
140813    4.289488e+09
3782      4.288060e+09
119677    4.275259e+09
39639     4.268432e+09
76996     4.259997e+09
59016     4.256650e+09
41210     4.254644e+09
Name: TCP DL Retrans. Vol (Bytes), dtype: float64

Bottom 10 TCP values:
 59717     2.0
125091    2.0
2850      4.0
39612     4.0
52489     4.0
60376     4.0
60426     4.0
75097     4.0
100314    4.0
143429    4.0
Name: TCP DL Retrans. Vol (Bytes), dtype: float64

Most frequent TCP value: 20809914.27034193

Top 10 RTT values:
 30168     96923.0
29929     64640.0
5989      54847.0
22851     26971.0
23455     26250.0
1373      25873.0
81279     25602.0
97320     25374.0
100583    24733.0
97914     20979.0
Name: Avg RTT DL (ms), dtype: float64

Bottom 10 RTT values:
 42613     0.0
52226     0.0
60152     0.0
61152     0.0
61345     0.0
103327    0.0
124541    0.0
142526    0.0
143878    0.0
71739     2.0
Name: Avg RTT DL (ms), dtype: float64



In [58]:
plt.figure(figsize=(200, 50))
sns.boxplot(x='Handset Type', y='Avg Bearer TP DL (kbps)', data=df)
plt.title('Distribution of Average Throughput per Handset Type')
plt.xlabel('Handset Type')
plt.ylabel('Average Throughput (kbps)')
plt.xticks(rotation=45)
plt.grid(axis='y', linestyle='--', alpha=0.7)
plt.tight_layout()
plt.show()


In [55]:
# Task 4.3: Distribution of average throughput per handset type in a table summary format
average_throughput_summary = df.groupby('Handset Type')['Avg Bearer TP DL (kbps)'].describe()
print("Distribution of Average Throughput per Handset Type:")
print(average_throughput_summary)


Distribution of Average Throughput per Handset Type:
                                                     count          mean  \
Handset Type                                                               
A-Link Telecom I. Cubot A5                             1.0  23184.000000   
A-Link Telecom I. Cubot Note Plus                      1.0   6527.000000   
A-Link Telecom I. Cubot Note S                         1.0   8515.000000   
A-Link Telecom I. Cubot Nova                           1.0  55667.000000   
A-Link Telecom I. Cubot Power                          1.0  69126.000000   
...                                                    ...           ...   
Zte Zte Blade C2 Smartphone Android By Sfr Star...     2.0     44.500000   
Zyxel Communicat. Lte7460                              1.0  39741.000000   
Zyxel Communicat. Sbg3600                              1.0  82818.000000   
Zyxel Communicat. Zyxel Wah7706                        1.0   1263.000000   
undefined                          

In [57]:
avg_tcp_per_handset = df.groupby('Handset Type')['TCP DL Retrans. Vol (Bytes)'].mean().sort_values(ascending=False)
print("Average TCP Retransmission per Handset Type:\n", avg_tcp_per_handset)


Average TCP Retransmission per Handset Type:
 Handset Type
Lg Lg-H635                                    9.117894e+08
Huawei Bln-Al10                               3.290646e+08
Asustek Asus Zenfone Selfie Zd551Kl           3.189534e+08
Samsung Galaxy Tab S3 (Sm-T825)               2.026297e+08
Huawei E5776S-32                              1.679920e+08
                                                  ...     
Tcl Communicatio. Nura 2                      7.500000e+01
Archos Sa Sense 55S                           6.600000e+01
Hmd Global Oy Nokia 6 Ds                      5.700000e+01
Microsoft Mobile. Rm-1062 Lumia 640 Xl Lte    4.500000e+01
Gemalto M2M Gmbh Cinterion Ehs5-E             1.200000e+01
Name: TCP DL Retrans. Vol (Bytes), Length: 1394, dtype: float64


In [41]:
avg_tcp_per_handset = df.groupby('Handset Type')['TCP DL Retrans. Vol (Bytes)'].mean().sort_values(ascending=False)
print("Average TCP Retransmission per Handset Type:\n", avg_tcp_per_handset)

# Task 4.4: K-means clustering for user segmentation
# Prepare data for clustering
X = customer_info[['TCP DL Retrans. Vol (Bytes)', 'Avg RTT DL (ms)', 'Avg Bearer TP DL (kbps)']]
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

# Perform K-means clustering
kmeans = KMeans(n_clusters=3, random_state=42)
kmeans.fit(X_scaled)
customer_info['Cluster'] = kmeans.labels_

# Description of clusters
cluster_summary = customer_info.groupby('Cluster').agg({
    'TCP DL Retrans. Vol (Bytes)': ['min', 'max', 'mean'],
    'Avg RTT DL (ms)': ['min', 'max', 'mean'],
    'Avg Bearer TP DL (kbps)': ['min', 'max', 'mean']
})
print("\nCluster summary:")
print(cluster_summary)

Average TCP Retransmission per Handset Type:
 Handset Type
Lg Lg-H635                                    9.117894e+08
Huawei Bln-Al10                               3.290646e+08
Asustek Asus Zenfone Selfie Zd551Kl           3.189534e+08
Samsung Galaxy Tab S3 (Sm-T825)               2.026297e+08
Huawei E5776S-32                              1.679920e+08
                                                  ...     
Tcl Communicatio. Nura 2                      7.500000e+01
Archos Sa Sense 55S                           6.600000e+01
Hmd Global Oy Nokia 6 Ds                      5.700000e+01
Microsoft Mobile. Rm-1062 Lumia 640 Xl Lte    4.500000e+01
Gemalto M2M Gmbh Cinterion Ehs5-E             1.200000e+01
Name: TCP DL Retrans. Vol (Bytes), Length: 1394, dtype: float64

Cluster summary:
        TCP DL Retrans. Vol (Bytes)                              \
                                min           max          mean   
Cluster                                                           
0        